In [128]:
import numpy as np
import pandas as pd

In [129]:
pd.set_option('display.max_rows',None)
#pd.reset_option('display.max_rows')
#pd.set_option('display.max_rows',1000)
pd.set_option('display.max_columns',None)

In [130]:
np.random.seed(40)
n=5000

In [131]:
speed=np.random.normal(45,10,n)

In [132]:
speed

array([38.92452303, 43.73863585, 38.15393641, ..., 50.06198914,
       49.75103874, 43.49155577])

In [133]:
fatigue=np.random.uniform(0,10,n)
traffic=np.random.uniform(0,1,n)
visibility=np.random.normal(600,200,n)
brake_events=np.random.poisson(3,n)
school_hour=np.random.randint(5,18,n)
weather=np.random.choice(["clear","rain","fog"],size=n,p=[0.55,0.25,0.20])

In [134]:
speed+=np.random.normal(0,5,n)
visibility+=np.random.normal(0,50,n)

In [135]:
outliers=np.random.choice(n,50)
speed[outliers]=np.random.uniform(60,80,50)

In [136]:
df=pd.DataFrame({
    "speed_km/h":speed,
    "fatigue_score": fatigue,
    "traffic_density":traffic,
    "visibility":visibility,
    "brake_events":brake_events,
    "school_timing":school_hour,
    "weather":weather})
df

speed_km/h  fatigue_score  traffic_density   visibility  brake_events  \
0      48.468695       0.673716         0.413108   574.021792             6   
1      47.741877       5.688582         0.213230   680.280772             0   
2      38.788140       4.000647         0.233332   803.822498             6   
3      60.633978       8.781579         0.894332   748.719389             2   
4      25.605656       7.387950         0.444493   692.355047             2   
5      43.730582       9.047899         0.368847   582.580852             3   
6      63.933368       8.550320         0.357959   492.984499             2   
7      50.990318       9.139133         0.761416   903.605734             3   
8      52.727220       1.257925         0.543282   554.627348             4   
9      57.050457       7.499790         0.511923   791.050996             8   
10     39.654886       3.074433         0.733826   839.065823             1   
11     46.998838       9.195472         0.824641   882.158964             6   
12     57.728312       8.141738         0.839604   722.904584             0   
13     56.268779       6.310509         0.723660   568.903947             3   
14     31.897145       2.908078         0.040212   715.627975             2   
15     43.649151       1.730355         0.794418   494.595343             1   
16     35.521730       0.810758         0.215119   378.303507             1   
17     40.338201       3.323967         0.963092   711.058564             2   
18     51.214927       7.012025         0.055526   517.497310             2   
19     75.130984       8.764849         0.522819   866.908325             5   
20     47.933046       5.271105         0.795895   568.775227             2   
21     43.164106       2.194084         0.331040   491.495165             1   
22     47.905004       7.824051         0.904968   499.289412             2   
23     54.083037       6.014529         0.676719   513.642800             1   
24     56.725916       0.132652         0.621723   405.312793             2   
25     44.245745       6.588063         0.135074   739.296369             4   
26     68.086517       3.267564         0.548266   180.734393             4   
27     46.460588       3.288062         0.067638   885.584880             2   
28     35.457644       7.844783         0.266076   529.148992             5   
29     63.251951       2.481441         0.545470   270.233067             0   
30     46.516331       1.392150         0.434086   266.004410             2   
31     39.763033       5.217861         0.195984   495.253660             0   
32     41.611730       5.867594         0.807393   736.911031             4   
33     47.939523       6.819375         0.151402   766.443183             5   
34     34.490481       3.259771         0.643093   500.573252             4   
35     47.804102       2.785396         0.014591   504.528115             3   
36     19.291257       6.331215         0.569361   217.872507             1   
37     34.662111       3.254449         0.000016   490.168269             3   
38     36.351972       6.283155         0.751677   661.749007             4   
39     35.154782       7.418316         0.217164   714.380085             4   
40     53.424750       9.777235         0.278367   582.914648             3   
41     56.225701       4.152929         0.723849   495.194194             3   
42     41.505865       5.290951         0.776899   357.863605             3   
43     39.576227       2.179271         0.984812   637.274187             2   
44     61.315638       4.760722         0.190494   129.146099             2   
45     43.254660       9.903296         0.050520   472.445489             4   
46     38.282793       9.422216         0.666013   613.797512             1   
47     47.378920       0.694929         0.015529   962.996162             5   
48     41.957261       5.014039         0.179688   433.619351             3   
49     63.168448       9.565254         0.578530   470.4

In [154]:
df["overspeeding"]=(df["speed_km/h"]>50).astype(int)

In [162]:
df["traffic_pressure"]=df["traffic_density"]*df["speed_km/h"]
df["visibility_risk"]=1/(df["visibility"]+1)
df["rush_hours"]=df["school_timing"].isin([8,9,10,16,17,18]).astype(int)
df["fatigue_speed_risk"]=(df["speed_km/h"]*df["fatigue_score"])
df["harsh_break"]=(df["brake_events"]>8).astype(int)
weather_risk={"clear":1,"rain":1.5,"fog":2}
df["weather_risk"]=df["weather"].map(weather_risk)


In [166]:
risk_score=(
    0.3*df["speed_km/h"]+
    0.25*df["fatigue_score"]+
    0.2*df["traffic_density"]+
    0.15*df["visibility_risk"]+
    0.1*df["brake_events"])

In [172]:
prob=1/(1+np.exp(-risk_score))
df["accident_risk"]=(prob>0.5).astype(int)

In [174]:
df

speed_km/h  fatigue_score  traffic_density   visibility  brake_events  \
0      48.468695       0.673716         0.413108   574.021792             6   
1      47.741877       5.688582         0.213230   680.280772             0   
2      38.788140       4.000647         0.233332   803.822498             6   
3      60.633978       8.781579         0.894332   748.719389             2   
4      25.605656       7.387950         0.444493   692.355047             2   
5      43.730582       9.047899         0.368847   582.580852             3   
6      63.933368       8.550320         0.357959   492.984499             2   
7      50.990318       9.139133         0.761416   903.605734             3   
8      52.727220       1.257925         0.543282   554.627348             4   
9      57.050457       7.499790         0.511923   791.050996             8   
10     39.654886       3.074433         0.733826   839.065823             1   
11     46.998838       9.195472         0.824641   882.158964             6   
12     57.728312       8.141738         0.839604   722.904584             0   
13     56.268779       6.310509         0.723660   568.903947             3   
14     31.897145       2.908078         0.040212   715.627975             2   
15     43.649151       1.730355         0.794418   494.595343             1   
16     35.521730       0.810758         0.215119   378.303507             1   
17     40.338201       3.323967         0.963092   711.058564             2   
18     51.214927       7.012025         0.055526   517.497310             2   
19     75.130984       8.764849         0.522819   866.908325             5   
20     47.933046       5.271105         0.795895   568.775227             2   
21     43.164106       2.194084         0.331040   491.495165             1   
22     47.905004       7.824051         0.904968   499.289412             2   
23     54.083037       6.014529         0.676719   513.642800             1   
24     56.725916       0.132652         0.621723   405.312793             2   
25     44.245745       6.588063         0.135074   739.296369             4   
26     68.086517       3.267564         0.548266   180.734393             4   
27     46.460588       3.288062         0.067638   885.584880             2   
28     35.457644       7.844783         0.266076   529.148992             5   
29     63.251951       2.481441         0.545470   270.233067             0   
30     46.516331       1.392150         0.434086   266.004410             2   
31     39.763033       5.217861         0.195984   495.253660             0   
32     41.611730       5.867594         0.807393   736.911031             4   
33     47.939523       6.819375         0.151402   766.443183             5   
34     34.490481       3.259771         0.643093   500.573252             4   
35     47.804102       2.785396         0.014591   504.528115             3   
36     19.291257       6.331215         0.569361   217.872507             1   
37     34.662111       3.254449         0.000016   490.168269             3   
38     36.351972       6.283155         0.751677   661.749007             4   
39     35.154782       7.418316         0.217164   714.380085             4   
40     53.424750       9.777235         0.278367   582.914648             3   
41     56.225701       4.152929         0.723849   495.194194             3   
42     41.505865       5.290951         0.776899   357.863605             3   
43     39.576227       2.179271         0.984812   637.274187             2   
44     61.315638       4.760722         0.190494   129.146099             2   
45     43.254660       9.903296         0.050520   472.445489             4   
46     38.282793       9.422216         0.666013   613.797512             1   
47     47.378920       0.694929         0.015529   962.996162             5   
48     41.957261       5.014039         0.179688   433.619351             3   
49     63.168448       9.565254         0.578530   470.4

In [176]:
df.to_csv("school_bus_accident.csv",index=False)